In [3]:
from io import BytesIO
from zipfile import ZipFile
from urllib.request import urlopen
import geopandas as gpd
from io import StringIO
# or: requests.get(url).content
from shapely.geometry import Point, LineString
import boto3
import pandas as pd
import pygris
import pysal
from libpysal.weights import Queen

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

# Plan
- Download pygris library for census data
- Gather census blocks in TriMet counties
- intersect census blocks with trimet route buffer
- create to:from matrix for all combinations of census blocks
- develop method to keep track of census block combos that have been used
- each game picks a new combination and randomly generates a point within those census blocks

In [4]:
block_group_list = [pygris.block_groups(cb=True, state='OR', county=x, year=2021) for x in ['Multnomah','Clackamas','Washington']]

Using FIPS code '41' for input 'OR'
Using FIPS code '051' for input 'Multnomah'
Using FIPS code '41' for input 'OR'
Using FIPS code '005' for input 'Clackamas'
Using FIPS code '41' for input 'OR'
Using FIPS code '067' for input 'Washington'


In [5]:
trimet_block_groups = pd.concat(block_group_list)

In [6]:
trimet_block_groups.head(200).explore()

In [7]:
trimet_block_groups.crs

<Geographic 2D CRS: EPSG:4269>
Name: NAD83
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: North America - onshore and offshore: Canada - Alberta; British Columbia; Manitoba; New Brunswick; Newfoundland and Labrador; Northwest Territories; Nova Scotia; Nunavut; Ontario; Prince Edward Island; Quebec; Saskatchewan; Yukon. Puerto Rico. United States (USA) - Alabama; Alaska; Arizona; Arkansas; California; Colorado; Connecticut; Delaware; Florida; Georgia; Hawaii; Idaho; Illinois; Indiana; Iowa; Kansas; Kentucky; Louisiana; Maine; Maryland; Massachusetts; Michigan; Minnesota; Mississippi; Missouri; Montana; Nebraska; Nevada; New Hampshire; New Jersey; New Mexico; New York; North Carolina; North Dakota; Ohio; Oklahoma; Oregon; Pennsylvania; Rhode Island; South Carolina; South Dakota; Tennessee; Texas; Utah; Vermont; Virginia; Washington; West Virginia; Wisconsin; Wyoming. US Virgin Islands. British Virgin Islands

In [8]:
bg_crs = trimet_block_groups.crs

In [9]:
tm_route_buffer = gpd.read_file("tm_route_buffer_bounds.geojson")
tm_route_buffer

description  \
0  trimet_route_buffer_boundary   

                                            geometry  
0  POLYGON ((-122.85454 45.36697, -122.85454 45.3...

In [10]:
tm_route_buffer.explore()

In [11]:
tm_route_buffer.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [12]:
tm_route_buffer_proj = tm_route_buffer.to_crs(bg_crs)

In [39]:
trimet_block_groups_intersection = gpd.overlay(tm_route_buffer_proj,trimet_block_groups, how='intersection')

In [40]:
trimet_block_groups_intersection['index_num'] = trimet_block_groups_intersection.index

In [41]:
trimet_block_groups_intersection.head(2)

description STATEFP COUNTYFP TRACTCE BLKGRPCE  \
0  trimet_route_buffer_boundary      41      051  007201        1   
1  trimet_route_buffer_boundary      41      051  009703        3   

                AFFGEOID         GEOID NAME       NAMELSAD LSAD    ALAND  \
0  1500000US410510072011  410510072011    1  Block Group 1   BG  4537967   
1  1500000US410510097033  410510097033    3  Block Group 3   BG   400770   

    AWATER                                           geometry  index_num  
0  5048935  POLYGON ((-122.73176 45.62844, -122.73176 45.6...          0  
1        0  POLYGON ((-122.49014 45.51476, -122.49015 45.5...          1

In [50]:
trimet_block_groups_intersection.to_file("tm_route_buffer_blockgroup.geojson", driver="GeoJSON")

In [42]:
trimet_block_groups_intersection.explore()

In [43]:
w_queen = Queen.from_dataframe(trimet_block_groups_intersection, use_index=True)

In [44]:
w_queen.neighbors[0]

[304, 92, 350]

In [45]:
neighbor_df = pd.DataFrame.from_dict([w_queen.neighbors]).T.rename(columns={0:'neighbors'})
neighbor_df.head(3)

neighbors
0                      [304, 92, 350]
1  [518, 344, 89, 490, 139, 414, 479]
2  [112, 80, 404, 405, 406, 118, 364]

In [46]:
trimet_block_groups_w_neighbors = trimet_block_groups_intersection.merge(neighbor_df
                                                                         , how='left'
                                                                         , left_index=True
                                                                         , right_index=True)
trimet_block_groups_w_neighbors.head(3)

description STATEFP COUNTYFP TRACTCE BLKGRPCE  \
0  trimet_route_buffer_boundary      41      051  007201        1   
1  trimet_route_buffer_boundary      41      051  009703        3   
2  trimet_route_buffer_boundary      41      051  003302        1   

                AFFGEOID         GEOID NAME       NAMELSAD LSAD    ALAND  \
0  1500000US410510072011  410510072011    1  Block Group 1   BG  4537967   
1  1500000US410510097033  410510097033    3  Block Group 3   BG   400770   
2  1500000US410510033021  410510033021    1  Block Group 1   BG   333947   

    AWATER                                           geometry  index_num  \
0  5048935  POLYGON ((-122.73176 45.62844, -122.73176 45.6...          0   
1        0  POLYGON ((-122.49014 45.51476, -122.49015 45.5...          1   
2        0  POLYGON ((-122.65467 45.55548, -122.64991 45.5...          2   

                            neighbors  
0                      [304, 92, 350]  
1  [518, 344, 89, 490, 139, 414, 479]  
2  [112, 80, 404, 405, 406, 118, 364]

In [47]:
trimet_block_groups_w_neighbors.iloc[0]['neighbors']

[304, 92, 350]

In [48]:
trimet_block_groups_w_neighbors.iloc[trimet_block_groups_w_neighbors.iloc[0]['neighbors']]

description STATEFP COUNTYFP TRACTCE BLKGRPCE  \
304  trimet_route_buffer_boundary      41      051  007201        2   
92   trimet_route_buffer_boundary      41      051  007202        2   
350  trimet_route_buffer_boundary      41      051  007202        3   

                  AFFGEOID         GEOID NAME       NAMELSAD LSAD     ALAND  \
304  1500000US410510072012  410510072012    2  Block Group 2   BG    894910   
92   1500000US410510072022  410510072022    2  Block Group 2   BG    439640   
350  1500000US410510072023  410510072023    3  Block Group 3   BG  22080793   

      AWATER                                           geometry  index_num  \
304  2309855  POLYGON ((-122.67546 45.61695, -122.67538 45.6...        304   
92    354101  POLYGON ((-122.65548 45.60281, -122.65548 45.6...         92   
350  6462065  MULTIPOLYGON (((-122.77710 45.61706, -122.7771...        350   

                                             neighbors  
304                                       [0, 92, 350]  
92                                  [0, 304, 320, 350]  
350  [0, 320, 69, 422, 91, 92, 304, 379, 20, 342, 3...

In [49]:
@interact(index=list(trimet_block_groups_w_neighbors.index))
def h(index=0):
    one_block = trimet_block_groups_w_neighbors.iloc[[index]]
    m = one_block.explore(color='blue')
    neighbor_blocks = trimet_block_groups_w_neighbors.iloc[trimet_block_groups_w_neighbors.iloc[index]['neighbors']]
    neighbor_blocks.explore(m=m, color='red')
    return m

interactive(children=(Dropdown(description='index', options=(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14,…

In [22]:
trimet_block_groups_w_neighbors['neighbors_and_self'] = trimet_block_groups_w_neighbors.apply(lambda x: x['neighbors']+[x.name],axis=1)

In [23]:
trimet_block_groups_w_neighbors.head(3)

description STATEFP COUNTYFP TRACTCE BLKGRPCE  \
0  trimet_route_buffer_boundary      41      051  007201        1   
1  trimet_route_buffer_boundary      41      051  009703        3   
2  trimet_route_buffer_boundary      41      051  003302        1   

                AFFGEOID         GEOID NAME       NAMELSAD LSAD    ALAND  \
0  1500000US410510072011  410510072011    1  Block Group 1   BG  4537967   
1  1500000US410510097033  410510097033    3  Block Group 3   BG   400770   
2  1500000US410510033021  410510033021    1  Block Group 1   BG   333947   

    AWATER                                           geometry  \
0  5048935  POLYGON ((-122.73176 45.62844, -122.73176 45.6...   
1        0  POLYGON ((-122.49014 45.51476, -122.49015 45.5...   
2        0  POLYGON ((-122.65467 45.55548, -122.64991 45.5...   

                            neighbors                     neighbors_and_self  
0                      [304, 92, 350]                      [304, 92, 350, 0]  
1  [518, 344, 89, 490, 139, 414, 479]  [518, 344, 89, 490, 139, 414, 479, 1]  
2  [112, 80, 404, 405, 406, 118, 364]  [112, 80, 404, 405, 406, 118, 364, 2]

In [25]:
trimet_block_groups_w_neighbors_for_join = trimet_block_groups_w_neighbors[['index_num']].copy()

In [26]:
trimet_block_groups_w_neighbors_self_join = trimet_block_groups_w_neighbors.merge(trimet_block_groups_w_neighbors_for_join, how='cross')
trimet_block_groups_w_neighbors_self_join.head(2)

description STATEFP COUNTYFP TRACTCE BLKGRPCE  \
0  trimet_route_buffer_boundary      41      051  007201        1   
1  trimet_route_buffer_boundary      41      051  007201        1   

                AFFGEOID         GEOID NAME       NAMELSAD LSAD    ALAND  \
0  1500000US410510072011  410510072011    1  Block Group 1   BG  4537967   
1  1500000US410510072011  410510072011    1  Block Group 1   BG  4537967   

    AWATER                                           geometry       neighbors  \
0  5048935  POLYGON ((-122.73176 45.62844, -122.73176 45.6...  [304, 92, 350]   
1  5048935  POLYGON ((-122.73176 45.62844, -122.73176 45.6...  [304, 92, 350]   

  neighbors_and_self  index_num_x  index_num_y  
0  [304, 92, 350, 0]            0            0  
1  [304, 92, 350, 0]            0            1

In [33]:
trimet_block_groups_w_neighbors_self_join.shape

(1162084, 17)

In [80]:
trimet_block_groups_combos_reduced = (trimet_block_groups_w_neighbors_self_join[
    trimet_block_groups_w_neighbors_self_join.apply(lambda x: x['index_num_y'] not in x['neighbors_and_self'], axis=1)]
    [['index_num_x','index_num_y']].rename(columns={'index_num_x':'origin_index','index_num_y':'destination_index'}).copy())

In [81]:
trimet_block_groups_combos_reduced.head(3)

origin_index  destination_index
1             0                  1
2             0                  2
3             0                  3

In [82]:
trimet_block_groups_combos_reduced.shape

(1154594, 2)

In [83]:
trimet_block_groups_combos_reduced['combination_used'] = 0
trimet_block_groups_combos_reduced['time_used'] = pd.NaT

In [84]:
trimet_block_groups_combos_reduced.to_csv("trimet_block_groups_combos_tracking.csv")

In [85]:
trimet_block_groups_combos_reduced.head(2)

origin_index  destination_index  combination_used time_used
1             0                  1                 0       NaT
2             0                  2                 0       NaT

In [87]:
trimet_block_groups_combos_reduced.shape[0]

1154594

In [94]:
trimet_block_groups_combos_reduced.sample(1)

origin_index  destination_index  combination_used time_used
1087361          1008                737                 0       NaT

In [88]:
import datetime

Thinking about not allowing the same origin twice in a row but let's see how the random index choice works before implementing anything "crazy"

In [89]:
trimet_block_groups_combos_reduced.loc[(trimet_block_groups_combos_reduced['origin_index']==2)&(trimet_block_groups_combos_reduced['destination_index']==50),'time_used'] = datetime.datetime.now()

In [93]:
most_recent_origin = trimet_block_groups_combos_reduced.sort_values(['time_used']).head(1)['origin_index'].to_numpy()[0]

2